In [1]:
import re
from tqdm import tqdm
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import torch
import string


In [2]:
# os.environ['CUDA_LAUNCH_BLOCKING'] = '1'
if torch.cuda.is_available(): 
    device = torch.device("cuda")
    print(f'There are {torch.cuda.device_count()} GPU(s) available.')
    print('Device name:', torch.cuda.get_device_name(0))
else:
    print('No GPU available, using the CPU instead.')
    device = torch.device("cpu")


There are 2 GPU(s) available.
Device name: GeForce RTX 2080 SUPER


In [3]:
df_sentiment = pd.read_csv('../Data/THR_DLR_CLA_V2_OTHER_LABELS_REMOVED_New.csv')
df_sentiment =  df_sentiment.drop(columns='Crime/Violence-Other')
df_sentiment

News_ID                                         News Title  \
0       23675  ตร.นนท์จับหนุ่มแท็กซี่ขโมยเนื้อหมูของร้านตามสั...   
1       23676  ครอบครัว "ฮ้อแสงชัย" เชื่อคดี "เบนซ์ชนฟอร์ด" จ...   
2       23677  ตร.แจง ดารากุเรื่องเป็นเซียนหวย อาจเข้าข่ายผิด...   
3       23678  หนุ่มชาวบ้านที่ถูกยิงดับใต้สะพานที่บาเจาะ ตร.ค...   
4       23679  ผกก.สายไหม มอบสิ่งของผู้สูงอายุ เนื่องในวันเฉล...   
...       ...                                                ...   
1974    19170  'แก๊งเสียไม่ได้'ระส่ำ ตร.หิ้ว'ไอ้คิว'หัวหน้าแก...   
1975    19171  ล่า2ตร.นครบาลเอี่ยวรีดทรัพย์ ออกหมายจับพร้อมพว...   
1976    19172  โหด!จ่อยิงหนุ่ม5นัดซ้อน เคลียร์ปัญหามือปืนไม่ล...   
1977    19173  สยบหนุ่มคลั่งง้อเมียไม่คืนดี ซิ่งรถยิงใส่ตร.เจ...   
1978    19174  ออกหมายจับมือปืนยิงเพื่อนซี้ ปมแค้นหักหลัง-เอา...   

                                             News_Intro  \
0     ตำรวจ สภ.รัตนาธิเบศร์ จับกุมโชเฟอร์แท็กซี่ตามห...   
1     น้องสาวและครอบครัวฮ้อแสงชัย ขอบคุณกระบวนการยุต...   
2     รองโฆษก ตร.แจงกรณีสื่อแฉดาราสร้างเรื่องหลอกลวง...   
3     พบศพหนุ่มวัย 22 ปี ถูกยิงด้วยปืน 9 มม. ตาย 1 ศ...   
4     ผกก.สน.สายไหม นำทีมข้าราชการตำรวจในสังกัด และเ...   
...                                                 ...   
1974  รวบ "ไอ้คิว" หัวหน้าแก๊งเสียไม่ได้ พยายามฆ่าผู...   
1975  รองโฆษก ตร. เผยมีตำรวจเอี่ยวรีดทรัพย์ 2 นาย พื...   
1976  หนุ่มสงขลาวัยเบญจเพสดับรถ จยย. ที่หน้าบ้านพักข...   
1977  ไล่ล่าระทึก!! พ่อค้ารับซื้อผลไม้ง้อเมียไม่สำเร...   
1978  ตำรวจรู้ตัวมือปืนก่อเหตุยิงหนุ่มวัย 25 ปีโหดเห...   

                                              News_Desc  \
0     ตำรวจ สภ.รัตนาธิเบศร์ จับกุมโชเฟอร์แท็กซี่ตามห...   
1     น้องสาวและครอบครัวฮ้อแสงชัย ขอบคุณกระบวนการยุต...   
2     รองโฆษก ตร.แจงกรณีสื่อแฉดาราสร้างเรื่องหลอกลวง...   
3     พบศพหนุ่มวัย 22 ปี ถูกยิงด้วยปืน 9 มม. ตาย 1 ศ...   
4     ผกก.สน.สายไหม นำทีมข้าราชการตำรวจในสังกัด และเ...   
...                                                 ...   
1974  เมื่อวันที่ 1 พ.ค. พ.ต.อ.ธีระชัย ชำนาญหมอ รอง ...   
1975  เมื่อวันที่ 1 พ.ค. ที่สำนักงานตำรวจแห่งชาติ (ต...   
1976  เมื่อวันที่ 2 พ.ค. ร.ต.อ.นรินทร์ นิลวงศ์ รอง ส...   
1977  ผู้สื่อข่าวรายงานว่า เวลา 20.00 น. วันที่ 1 พ....   
1978  กรณีนายรังสรรค์ กรรณกานนท์ อายุ 25 ปี ถูกคนร้า...   

                                               News_All  Gambling  Murder  \
0     ตร.นนท์จับหนุ่มแท็กซี่ขโมยเนื้อหมูของร้านตามสั...         0       0   
1     ครอบครัว "ฮ้อแสงชัย" เชื่อคดี "เบนซ์ชนฟอร์ด" จ...         0       0   
2     ตร.แจง ดารากุเรื่องเป็นเซียนหวย อาจเข้าข่ายผิด...         0       0   
3     หนุ่มชาวบ้านที่ถูกยิงดับใต้สะพานที่บาเจาะ ตร.ค...         0       1   
4     ผกก.สายไหม มอบสิ่งของผู้สูงอายุ เนื่องในวันเฉล...         0       0   
...                                                 ...       ...     ...   
1974  'แก๊งเสียไม่ได้'ระส่ำ ตร.หิ้ว'ไอ้คิว'หัวหน้าแก...         0       1   
1975  ล่า2ตร.นครบาลเอี่ยวรีดทรัพย์ ออกหมายจับพร้อมพว...         0       0   
1976  โหด!จ่อยิงหนุ่ม5นัดซ้อน เคลียร์ปัญหามือปืนไม่ล...         0       1   
1977  สยบหนุ่มคลั่งง้อเมียไม่คืนดี ซิ่งรถยิงใส่ตร.เจ...         0       1   
1978  ออกหมายจับมือปืนยิงเพื่อนซี้ ปมแค้นหักหลัง-เอา...         0       1   

      Sexual Abuse  Theft/Burglary  Drug  Battery/Assault  Accident  Non-Crime  
0                0               1     0                0         0          0  
1                0               0     0                0         1          0  
2                0               0     0                0         0          1  
3                0               0     0                0         0          0  
4                0               0     0                0         0          1  
...            ...             ...   ...              ...       ...        ...  
1974             0               0     1                1         0          0  
1975             0               1     1                0         0          0  
1976             0               0     0                0         0          0  
1977             0               0  

In [4]:
def clean_msg(msg):
    # ลบ text ที่อยู่ในวงเล็บ <> ทั้งหมด
    msg = re.sub(r'<.*?>','', msg)
    # ลบ hashtag
    msg = re.sub(r'#','',msg)
    # ลบ space
    msg = re.sub(r' ','',msg)
    # ลบ เครื่องหมายคำพูด (punctuation)
    for c in string.punctuation:
        msg = re.sub(r'\{}'.format(c),'',msg)
    # ลบ separator เช่น \n \t
    msg = ' '.join(msg.split())
    return msg

In [5]:
X = df_sentiment.iloc[:,4:5].values 
y = df_sentiment.iloc[:, 5:].values
clean_text_arr = []
for i in range(len(X)):
    clean_text = clean_msg(X[i][0])
    temp_arr = []
    temp_arr.append(clean_text)
    clean_text_arr.append(temp_arr)
# print(clean_text_arr)
X = np.array(clean_text_arr)

In [6]:
print(X)

[['ตรนนท์จับหนุ่มแท็กซี่ขโมยเนื้อหมูของร้านตามสั่งปมอดอยากจากพิษโควิดคลิปตำรวจสภรัตนาธิเบศร์จับกุมโชเฟอร์แท็กซี่ตามหมายจับหลังวงจรปิดจับภาพตอนก่อเหตุลักเนื้อหมูและไก่จากร้านอาหารตามสั่งสารภาพทำไปเพราะไม่มีจะกินรายได้ไม่พอเพราะพิษโควิด19ด้านผู้เสียหายให้อภัยเมื่อเวลา2130นวันที่2มิย63ที่สภานีตำรวจภูธรรัตนาธิเบศร์จนนทบุรีพตทอัศม์เดชมุ่งลือรองผกกสสพตทศุภชัยศรีศักดิ์สวสสรตอสุนทรหงษ์โยธีรองสวสสรตอสันติชัยดีพร้อมรองสวสสพร้อมด้วยกำลังเจ้าหน้าที่สืบสวนร่วมกันจับกุมตัวนายตำรวจสภรัตนาธิเบศร์จับกุมโชเฟอร์แท็กซี่ตามหมายจับหลังวงจรปิดจับภาพตอนก่อเหตุลักเนื้อหมูและไก่จากร้านอาหารตามสั่งสารภาพทำไปเพราะไม่มีจะกินรายได้ไม่พอเพราะพิษโควิด19ด้านผู้เสียหายให้อภัยเมื่อเวลา2130นวันที่2มิย63ที่สภานีตำรวจภูธรรัตนาธิเบศร์จนนทบุรีพตทอัศม์เดชมุ่งลือรองผกกสสพตทศุภชัยศรีศักดิ์สวสสรตอสุนทรหงษ์โยธีรองสวสสรตอสันติชัยดีพร้อมรองสวสสพร้อมด้วยกำลังเจ้าหน้าที่สืบสวนร่วมกันจับกุมตัวนายบุญมีสิมวงศ์อายุ39ปีอาชีพขับรถเเท็กซี่อยู่บ้านเลขที่551หมู่ที่2ตกุดตุ้มอเมืองจชัยภูมิผู้ต้องหาตามหมายจับศาลจังหวัดนนทบุรีที่จ24663ข้อหาร่วมกั

In [7]:
X_2d = np.array([text for text in X])
print(type(X_2d))

<class 'numpy.ndarray'>


In [8]:
from skmultilearn.model_selection import iterative_train_test_split

# Set seed for numpy
np.random.seed(42)
X_train, y_train, X_test, y_test = iterative_train_test_split(X, y, test_size=0.2)
# X_train, y_train, X_test, y_test = iterative_train_test_split(X_2d, y, test_size=0.2)
X_train, y_train, X_val, y_val = iterative_train_test_split(X_train, y_train, test_size=0.125)

In [9]:
X_train_new = np.array([text for sub in X_train for text in sub]) 
X_test_new = np.array([text for sub in X_test for text in sub]) 
X_val_new = np.array([text for sub in X_val for text in sub]) 

X_train_list = X_train_new.tolist()
X_test_list = X_test_new.tolist()
X_val_list = X_val_new.tolist()

In [10]:
print(X_train_new)

['ครอบครัวฮ้อแสงชัยเชื่อคดีเบนซ์ชนฟอร์ดจะเป็นบรรทัดฐานที่ดีแก่สังคมน้องสาวและครอบครัวฮ้อแสงชัยขอบคุณกระบวนการยุติธรรมภายหลังศาลฎีกาพิพากษายืนจำคุก4ปีไม่รอลงอาญาเสี่ยเจนภพคดีเบนซ์ชนรถฟอร์ดย่าง2ศพทำให้พี่สาวตายเชื่อคดีนี้จะเป็นบรรทัดฐานต่อสังคมกรณีเมื่อวันที่2มิย63ศาลจังหวัดพระนครศรีอยุธยาอ่านคำพิพากษาศาลฎีกาในคดีที่พนักงานอัยการจังหวัดพระนครศรีอยุธยาโจทก์นายไพบูลย์ถาวรนายทิวากรฮ้อแสงชัยกับพวกรวม4คนเป็นโจทก์ร่วมยื่นฟ้องนายเจนภพวีรพรเป็นจำเลยในความผิดฐานกระทำโดยประมาทเป็นเหตุให้ผู้อน้องสาวและครอบครัวฮ้อแสงชัยขอบคุณกระบวนการยุติธรรมภายหลังศาลฎีกาพิพากษายืนจำคุก4ปีไม่รอลงอาญาเสี่ยเจนภพคดีเบนซ์ชนรถฟอร์ดย่าง2ศพทำให้พี่สาวตายเชื่อคดีนี้จะเป็นบรรทัดฐานต่อสังคมกรณีเมื่อวันที่2มิย63ศาลจังหวัดพระนครศรีอยุธยาอ่านคำพิพากษาศาลฎีกาในคดีที่พนักงานอัยการจังหวัดพระนครศรีอยุธยาโจทก์นายไพบูลย์ถาวรนายทิวากรฮ้อแสงชัยกับพวกรวม4คนเป็นโจทก์ร่วมยื่นฟ้องนายเจนภพวีรพรเป็นจำเลยในความผิดฐานกระทำโดยประมาทเป็นเหตุให้ผู้อื่นถึงแก่ความตายข่าวแนะนำจากกรณีเมื่อวันที่13มีนาคม2559จำเลยได้ขับรถเบนซ์รุ่นซีแอลเคสีดำทะเบียนษง33

In [11]:
print(X_train_list)

['ครอบครัวฮ้อแสงชัยเชื่อคดีเบนซ์ชนฟอร์ดจะเป็นบรรทัดฐานที่ดีแก่สังคมน้องสาวและครอบครัวฮ้อแสงชัยขอบคุณกระบวนการยุติธรรมภายหลังศาลฎีกาพิพากษายืนจำคุก4ปีไม่รอลงอาญาเสี่ยเจนภพคดีเบนซ์ชนรถฟอร์ดย่าง2ศพทำให้พี่สาวตายเชื่อคดีนี้จะเป็นบรรทัดฐานต่อสังคมกรณีเมื่อวันที่2มิย63ศาลจังหวัดพระนครศรีอยุธยาอ่านคำพิพากษาศาลฎีกาในคดีที่พนักงานอัยการจังหวัดพระนครศรีอยุธยาโจทก์นายไพบูลย์ถาวรนายทิวากรฮ้อแสงชัยกับพวกรวม4คนเป็นโจทก์ร่วมยื่นฟ้องนายเจนภพวีรพรเป็นจำเลยในความผิดฐานกระทำโดยประมาทเป็นเหตุให้ผู้อน้องสาวและครอบครัวฮ้อแสงชัยขอบคุณกระบวนการยุติธรรมภายหลังศาลฎีกาพิพากษายืนจำคุก4ปีไม่รอลงอาญาเสี่ยเจนภพคดีเบนซ์ชนรถฟอร์ดย่าง2ศพทำให้พี่สาวตายเชื่อคดีนี้จะเป็นบรรทัดฐานต่อสังคมกรณีเมื่อวันที่2มิย63ศาลจังหวัดพระนครศรีอยุธยาอ่านคำพิพากษาศาลฎีกาในคดีที่พนักงานอัยการจังหวัดพระนครศรีอยุธยาโจทก์นายไพบูลย์ถาวรนายทิวากรฮ้อแสงชัยกับพวกรวม4คนเป็นโจทก์ร่วมยื่นฟ้องนายเจนภพวีรพรเป็นจำเลยในความผิดฐานกระทำโดยประมาทเป็นเหตุให้ผู้อื่นถึงแก่ความตายข่าวแนะนำจากกรณีเมื่อวันที่13มีนาคม2559จำเลยได้ขับรถเบนซ์รุ่นซีแอลเคสีดำทะเบียนษง33

In [12]:
# M-BERT uses different tokenizer from WangChanBERT
# https://huggingface.co/bert-base-multilingual-uncased
from transformers import BertTokenizer,BertModel

tokenizer = BertTokenizer.from_pretrained('bert-base-multilingual-cased')

def preprocessing_for_bert(data):

    input_ids = []
    attention_masks = []

    for sent in data:
        encoded_sent = tokenizer.encode_plus(
            #text=text_preprocessing(sent),  
            text=sent,
            add_special_tokens=True,        
            max_length=MAX_LEN,
            truncation=True,             
            padding='max_length',         
            #return_tensors='pt',           
            return_attention_mask=True      
        )
        
        input_ids.append(encoded_sent.get('input_ids'))
        attention_masks.append(encoded_sent.get('attention_mask'))

    input_ids = torch.tensor(input_ids)
    attention_masks = torch.tensor(attention_masks)

    return input_ids, attention_masks

2022-01-05 16:12:01.404335: I tensorflow/stream_executor/platform/default/dso_loader.cc:53] Successfully opened dynamic library libcudart.so.11.0


In [13]:
all_texts = np.concatenate([X_train_list, X_test_list, X_val_list])

In [14]:
# print(all_texts)

In [15]:
encoded_texts = [tokenizer.encode(sent, add_special_tokens=True,max_length=512,truncation=True) for sent in all_texts]

In [16]:
# print(encoded_texts)

In [17]:
max_len = max([len(sent) for sent in encoded_texts])
print('Max length: ', max_len)
avg_len = sum([len(sent) for sent in encoded_texts]) / len(encoded_texts)
print('Avg length: ', avg_len)

Max length:  512
Avg length:  35.62354724608388


In [18]:
print(encoded_texts[10])

[101, 100, 100, 1434, 20503, 28220, 34523, 31287, 37760, 100, 100, 100, 1434, 20503, 28220, 34523, 31287, 37760, 100, 100, 102]


In [19]:
MAX_LEN = 500 #due to the max length

token_ids = list(preprocessing_for_bert([X_train_new[0]])[0].squeeze().numpy())
print('Original: ', X_train_new[0])
print('\n')
print('Tokenized: ', tokenizer.tokenize(X_train_new[0]))
print('\n')
print('Token IDs: ', token_ids)

print('Tokenizing data...')
train_inputs, train_masks = preprocessing_for_bert(X_train_new)
val_inputs, val_masks = preprocessing_for_bert(X_val_new)

Original:  ครอบครัวฮ้อแสงชัยเชื่อคดีเบนซ์ชนฟอร์ดจะเป็นบรรทัดฐานที่ดีแก่สังคมน้องสาวและครอบครัวฮ้อแสงชัยขอบคุณกระบวนการยุติธรรมภายหลังศาลฎีกาพิพากษายืนจำคุก4ปีไม่รอลงอาญาเสี่ยเจนภพคดีเบนซ์ชนรถฟอร์ดย่าง2ศพทำให้พี่สาวตายเชื่อคดีนี้จะเป็นบรรทัดฐานต่อสังคมกรณีเมื่อวันที่2มิย63ศาลจังหวัดพระนครศรีอยุธยาอ่านคำพิพากษาศาลฎีกาในคดีที่พนักงานอัยการจังหวัดพระนครศรีอยุธยาโจทก์นายไพบูลย์ถาวรนายทิวากรฮ้อแสงชัยกับพวกรวม4คนเป็นโจทก์ร่วมยื่นฟ้องนายเจนภพวีรพรเป็นจำเลยในความผิดฐานกระทำโดยประมาทเป็นเหตุให้ผู้อน้องสาวและครอบครัวฮ้อแสงชัยขอบคุณกระบวนการยุติธรรมภายหลังศาลฎีกาพิพากษายืนจำคุก4ปีไม่รอลงอาญาเสี่ยเจนภพคดีเบนซ์ชนรถฟอร์ดย่าง2ศพทำให้พี่สาวตายเชื่อคดีนี้จะเป็นบรรทัดฐานต่อสังคมกรณีเมื่อวันที่2มิย63ศาลจังหวัดพระนครศรีอยุธยาอ่านคำพิพากษาศาลฎีกาในคดีที่พนักงานอัยการจังหวัดพระนครศรีอยุธยาโจทก์นายไพบูลย์ถาวรนายทิวากรฮ้อแสงชัยกับพวกรวม4คนเป็นโจทก์ร่วมยื่นฟ้องนายเจนภพวีรพรเป็นจำเลยในความผิดฐานกระทำโดยประมาทเป็นเหตุให้ผู้อื่นถึงแก่ความตายข่าวแนะนำจากกรณีเมื่อวันที่13มีนาคม2559จำเลยได้ขับรถเบนซ์รุ่นซีแอลเคสีดำทะ

In [20]:
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler

train_labels = torch.FloatTensor(y_train)
val_labels = torch.FloatTensor(y_val)

# batch size = 16, 32
batch_size = 10

train_data = TensorDataset(train_inputs, train_masks, train_labels)
train_sampler = RandomSampler(train_data)
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=batch_size)

val_data = TensorDataset(val_inputs, val_masks, val_labels)
val_sampler = SequentialSampler(val_data)
val_dataloader = DataLoader(val_data, sampler=val_sampler, batch_size=batch_size)

In [21]:
import torch
import torch.nn as nn
from transformers import CamembertForSequenceClassification , BertForSequenceClassification
from transformers import AdamW, get_linear_schedule_with_warmup
from transformers import CamembertConfig


def initialize_model(epochs=10):
#     configuration = CamembertConfig(max_position_embeddings=4096)
#     bert_classifier = CamembertForSequenceClassification(configuration)
    bert_classifier = BertForSequenceClassification.from_pretrained('bert-base-multilingual-cased')
    # bert_classifier = CamembertForSequenceClassification.from_pretrained('airesearch/wangchanberta-base-att-spm-uncased', num_labels=8, output_attentions=False, output_hidden_states=False)
#     bert_classifier = CamembertForSequenceClassification.from_pretrained('airesearch/wangchanberta-base-att-spm-uncased', num_labels=9, output_attentions=False, output_hidden_states=False)
#     bert_classifier.config = configuration
#     print(bert_classifier.config)
    # bert_classifier =nn.parallel.DistributedDataParallel(bert_classifier)
    bert_classifier = nn.DataParallel(bert_classifier)
    bert_classifier.to(device)
    
    # only adamW available in transformers (Pytorch)
    optimizer = AdamW(bert_classifier.parameters(),
                      lr=2e-5,    
                      betas=(0.9, 0.98), 
                      eps=1e-6,
                      weight_decay=0.1    
                )

    total_steps = len(train_dataloader) * epochs

    scheduler = get_linear_schedule_with_warmup(optimizer,
                                                num_warmup_steps=0,
                                                num_training_steps=total_steps
                )
    
    return bert_classifier, optimizer, scheduler

In [22]:
import random
import time

# Specify loss function
loss_fn = nn.BCELoss()
m = nn.Sigmoid()
training_stats = list()

def set_seed(seed_value=42):
    """Set seed for reproducibility.
    """
    random.seed(seed_value)
    np.random.seed(seed_value)
    torch.manual_seed(seed_value)
    torch.cuda.manual_seed_all(seed_value)

def train(model, train_dataloader, val_dataloader=None, epochs=10, evaluation=False):
    """Train the BertClassifier model.
    """
    # Start training loop
    print("Start training...\n")
    for epoch_i in range(epochs):
        # =======================================
        #               Training
        # =======================================
        # Print the header of the result table
        print(f"{'Epoch':^7} | {'Batch':^7} | {'Train Loss':^12} | {'Val Loss':^10} | {'Val Acc':^9} | {'Elapsed':^9}")
        print("-"*70)

        # Measure the elapsed time of each epoch
        t0_epoch, t0_batch = time.time(), time.time()

        # Reset tracking variables at the beginning of each epoch
        total_loss, batch_loss, batch_counts = 0, 0, 0

        # Put the model into the training mode
        model.train()

        # For each batch of training data...
        for step, batch in enumerate(train_dataloader):
            batch_counts +=1
            # Load batch to GPU
            b_input_ids, b_attn_mask, b_labels = tuple(t.to(device) for t in batch)

            # Zero out any previously calculated gradients
            model.zero_grad()

            # Perform a forward pass. This will return logits.
            outputs = model(b_input_ids, b_attn_mask)
            logits = outputs.logits

            # Compute loss and accumulate the loss values
            loss = loss_fn(m(logits), b_labels)
            batch_loss += loss.item()
            total_loss += loss.item()

            # Perform a backward pass to calculate gradients
            loss.backward()

            # Clip the norm of the gradients to 1.0 to prevent "exploding gradients"
            torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)

            # Update parameters and the learning rate
            optimizer.step()
            scheduler.step()

            # Print the loss values and time elapsed for every 20 batches
            if (step % 20 == 0 and step != 0) or (step == len(train_dataloader) - 1):
                # Calculate time elapsed for 20 batches
                time_elapsed = time.time() - t0_batch

                # Print training results
                print(f"{epoch_i + 1:^7} | {step:^7} | {batch_loss / batch_counts:^12.6f} | {'-':^10} | {'-':^9} | {time_elapsed:^9.2f}")

                # Reset batch tracking variables
                batch_loss, batch_counts = 0, 0
                t0_batch = time.time()
            torch.cuda.empty_cache()

        # Calculate the average loss over the entire training data
        avg_train_loss = total_loss / len(train_dataloader)

        print("-"*70)
        # =======================================
        #               Evaluation
        # =======================================
        if evaluation == True:
            # After the completion of each training epoch, measure the model's performance
            # on our validation set.
            val_loss, val_accuracy = evaluate(model, val_dataloader)

            # Print performance over the entire training data
            time_elapsed = time.time() - t0_epoch
            
            print(f"{epoch_i + 1:^7} | {'-':^7} | {avg_train_loss:^12.6f} | {val_loss:^10.6f} | {val_accuracy:^9.2f} | {time_elapsed:^9.2f}")
            print("-"*70)

            training_stats.append(
                {
                    'Epoch': epoch_i + 1,
                    'Training_Loss': avg_train_loss,
                    'Valid_Loss': val_loss,
                    'Valid_Accuracy': val_accuracy,
                    'Time_Elapsed': time_elapsed,
                }
            )

            torch.save(model.state_dict(), f'./Model/Fine_Tuning_BERT_GoEmotion_Sentiment_epoch{epoch_i+1}.h5')
        print("\n")
    
    print("Training complete!")


def evaluate(model, val_dataloader):
    """After the completion of each training epoch, measure the model's performance
    on our validation set.
    """
    # Put the model into the evaluation mode. The dropout layers are disabled during
    # the test time.
    model.eval()

    # Tracking variables
    val_accuracy = []
    val_loss = []

    # For each batch in our validation set...
    for batch in val_dataloader:
        # Load batch to GPU
        b_input_ids, b_attn_mask, b_labels = tuple(t.to(device) for t in batch)

        # Compute logits
        with torch.no_grad():
            outputs = model(b_input_ids, b_attn_mask)
            logits = outputs.logits

        # Compute loss
        #print(logits)
        #print(b_labels)
        loss = loss_fn(m(logits), b_labels)
        val_loss.append(loss.item())

        # Get the predictions
        # preds = torch.argmax(logits, dim=1).flatten()

        # Calculate the accuracy rate
        # accuracy = (preds == b_labels).cpu().numpy().mean() * 100
        accuracy = accuracy_thresh(logits.view(-1, 8), b_labels.view(-1, 8))
#         accuracy = accuracy_thresh(logits.view(-1, 9), b_labels.view(-1, 9))
        val_accuracy.append(accuracy)

    # Compute the average accuracy and loss over the validation set.
    val_loss = np.mean(val_loss)
    val_accuracy = np.mean(val_accuracy)

    return val_loss, val_accuracy

def accuracy_thresh(y_pred, y_true, thresh:float=0.5, sigmoid:bool=True):
    "Compute accuracy when `y_pred` and `y_true` are the same size."
    if sigmoid: 
        y_pred = y_pred.sigmoid()
    return ((y_pred > thresh) == y_true.byte()).float().mean().item()

In [23]:
set_seed(42)    # Set seed for reproducibility
bert_classifier, optimizer, scheduler = initialize_model(epochs=10)
train(bert_classifier, train_dataloader, val_dataloader, epochs=10, evaluation=True)

Some weights of the model checkpoint at bert-base-multilingual-cased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model ch

Start training...

 Epoch  |  Batch  |  Train Loss  |  Val Loss  |  Val Acc  |  Elapsed 
----------------------------------------------------------------------


Evaluate the model

In [ ]:
import torch.nn.functional as F

def bert_predict(model, test_dataloader):
    """Perform a forward pass on the trained BERT model to predict probabilities
    on the test set.
    """
    # Put the model into the evaluation mode. The dropout layers are disabled during
    # the test time.
    model.eval()

    all_logits = []

    # For each batch in our test set...
    for batch in test_dataloader:
        # Load batch to GPU
        b_input_ids, b_attn_mask = tuple(t.to(device) for t in batch)[:2]

        # Compute logits
        with torch.no_grad():
            outputs = model(b_input_ids, b_attn_mask)
            logits = outputs.logits
        all_logits.append(logits)
    
    # Concatenate logits from each batch
    all_logits = torch.cat(all_logits, dim=0)

    # Apply softmax to calculate probabilities
    probs = all_logits.sigmoid().cpu().numpy()

    return probs

In [ ]:
# Create a DataFrame from our training statistics.
df_stats = pd.DataFrame(data=training_stats)

# Use the 'epoch' as the row index.
df_stats = df_stats.set_index('Epoch')

# Display the table.
df_stats.sort_values(by=['Valid_Accuracy'], ascending=False)

In [ ]:
from sklearn.metrics import classification_report

# start from 5 since we need to avoid the news_data <Topic,Intro,Desc,All>
df_label_columns = df_sentiment.columns[5:]
label_names = list(df_label_columns)

print(classification_report(y_test, np.round(probs), target_names=label_names, zero_division=0))
df_label_columns

In [ ]:
import seaborn as sns

# Use plot styling from seaborn.
sns.set(style='darkgrid')

# Increase the plot size and font size.
sns.set(font_scale=1.5)
plt.rcParams["figure.figsize"] = (12,6)

# Plot the learning curve.
plt.plot(df_stats['Training_Loss'], 'b-o', label="Training")
plt.plot(df_stats['Valid_Loss'], 'g-o', label="Validation")

# Label the plot.
plt.title("Training & Validation Loss")
plt.xlabel("Epoch")
plt.ylabel("Loss")
plt.legend()
num_list = []
for i in range(100):
    num_list.append(i+1)
plt.xticks(num_list)

plt.show()

In [ ]:
# Hamming loss is the fraction of labels that are incorrectly predicted
from sklearn.metrics import hamming_loss

print(f"Hamming Loss: {hamming_loss(y_test, np.round(probs))}")